**Assignment-2-IR-part-2**

**Importing important library**

In [1]:
import pickle
import numpy as np
import pandas as pd
import math
import re
import requests
import cv2

import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
from collections import Counter
from bs4 import BeautifulSoup
from tensorflow.keras.applications import VGG16
from tensorflow.keras.applications.vgg16 import preprocess_input
from tensorflow.keras.models import Model

In [2]:
# Download NLTK resources
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


True

**connecting google drive**

In [3]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


**uploading the image_feature.pickle**

In [4]:
def open_pickle_file(file_path):
    try:
        with open(file_path, 'rb') as f:
            data_dict = pickle.load(f)
        return data_dict
    except FileNotFoundError:
        print("File not found.")
    except Exception as e:
        print("An error occurred:", e)
file_path = "/content/drive/MyDrive/IR_Assignment_2/image_feature.pickle"
data_dict = open_pickle_file(file_path)
if data_dict is not None:
    print("Data loaded successfully from pickle file:", data_dict)

Data loaded successfully from pickle file: {'https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg': array([ 0.       , 29.05717  , 38.6365   , ...,  3.0473914,  0.       ,
        0.       ], dtype=float32), 'https://images-na.ssl-images-amazon.com/images/I/71HSx4Y-5dL._SY88.jpg': array([ 0.       , 29.179907 , 35.848663 , ...,  3.1837215,  0.       ,
        0.       ], dtype=float32), 'https://images-na.ssl-images-amazon.com/images/I/71dVsYejzTL._SY88.jpg': array([ 0.       , 30.399292 , 37.19993  , ...,  3.1574123,  0.       ,
        0.       ], dtype=float32), 'https://images-na.ssl-images-amazon.com/images/I/71domStNfIL._SY88.jpg': array([ 0.       , 29.747963 , 36.861553 , ...,  3.2986622,  0.       ,
        0.       ], dtype=float32), 'https://images-na.ssl-images-amazon.com/images/I/71Md5ihUFLL._SY88.jpg': array([ 0.       , 30.620882 , 36.218494 , ...,  3.2881787,  0.       ,
        0.       ], dtype=float32), 'https://images-na.ssl-images-amazon.com/image

In [5]:
data_dict

{'https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg': array([ 0.       , 29.05717  , 38.6365   , ...,  3.0473914,  0.       ,
         0.       ], dtype=float32),
 'https://images-na.ssl-images-amazon.com/images/I/71HSx4Y-5dL._SY88.jpg': array([ 0.       , 29.179907 , 35.848663 , ...,  3.1837215,  0.       ,
         0.       ], dtype=float32),
 'https://images-na.ssl-images-amazon.com/images/I/71dVsYejzTL._SY88.jpg': array([ 0.       , 30.399292 , 37.19993  , ...,  3.1574123,  0.       ,
         0.       ], dtype=float32),
 'https://images-na.ssl-images-amazon.com/images/I/71domStNfIL._SY88.jpg': array([ 0.       , 29.747963 , 36.861553 , ...,  3.2986622,  0.       ,
         0.       ], dtype=float32),
 'https://images-na.ssl-images-amazon.com/images/I/71Md5ihUFLL._SY88.jpg': array([ 0.       , 30.620882 , 36.218494 , ...,  3.2881787,  0.       ,
         0.       ], dtype=float32),
 'https://images-na.ssl-images-amazon.com/images/I/71Isri9SEaL._SY88.jpg': array

In [6]:
print(data_dict["https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg"])
print(data_dict["https://images-na.ssl-images-amazon.com/images/I/81kc7eEmQ3L._SY88.jpg"])

[ 0.        29.05717   38.6365    ...  3.0473914  0.         0.       ]
[ 0.        29.543123  36.5442    ...  3.4314294  0.         0.       ]


In [7]:
def cosine_similarity(v1, v2):
    # Convert vectors to numpy arrays
    v1 = np.array(v1)
    v2 = np.array(v2)

    # Compute dot product
    dot_product = np.dot(v1, v2)

    # Compute magnitudes
    mag_v1 = np.linalg.norm(v1)
    mag_v2 = np.linalg.norm(v2)

    # Handle division by zero if one of the vectors is a zero vector
    if mag_v1 == 0 or mag_v2 == 0:
        return 0.0

    # Calculate cosine similarity
    similarity = dot_product / (mag_v1 * mag_v2)

    return similarity

**checking random cosine similarity**

In [9]:
import numpy as np

def cosine_similarity(v1, v2):
    # Convert vectors to numpy arrays
    v1 = np.array(v1)
    v2 = np.array(v2)

    # Compute dot product
    dot_product = np.dot(v1, v2)

    # Compute magnitudes
    mag_v1 = np.linalg.norm(v1)
    mag_v2 = np.linalg.norm(v2)

    # Handle division by zero if one of the vectors is a zero vector
    if mag_v1 == 0 or mag_v2 == 0:
        return 0.0

    # Calculate cosine similarity
    similarity = dot_product / (mag_v1 * mag_v2)

    return similarity


Cosine Similarity: 1.0


In [12]:
# Example vectors
vector1 = np.array(data_dict["https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg"])
vector2 = np.array(data_dict["https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg"])

# Reshape the vectors if needed (cosine_similarity function expects 2D arrays)

# Calculate cosine similarity
similarity = cosine_similarity(vector1, vector2)

print("Cosine Similarity:", similarity)

Cosine Similarity: 1.0


**calculating tf-idf score and store it in pickle file**

In [13]:
# Function to preprocess text
def preprocess_text(text):
    # Ensure text is a string
    text = str(text)
    # Remove HTML tags using BeautifulSoup
    clean_text = BeautifulSoup(text, 'html.parser').get_text()
    # Convert to lowercase
    clean_text = clean_text.lower()
    # Tokenize
    tokens = word_tokenize(clean_text)
    # Remove stopwords and non-alphabetic tokens
    stop_words = set(stopwords.words('english'))
    words = [word for word in tokens if word.isalpha() and word not in stop_words]
    # Lemmatization
    lemmatizer = WordNetLemmatizer()
    words = [lemmatizer.lemmatize(word) for word in words]
    return words

# Function to calculate term frequency (TF)
def calculate_tf(words):
    word_count = len(words)
    term_frequency = {}
    word_freq = Counter(words)
    for word in word_freq:
        term_frequency[word] = word_freq[word] / word_count
    return term_frequency

# Function to calculate inverse document frequency (IDF)
def calculate_idf(data):
    total_documents = len(data)
    idf = {}
    for index, row in data.iterrows():
        review = row['Review Text']
        words = set(preprocess_text(review))
        for word in words:
            idf[word] = idf.get(word, 0) + 1
    for word in idf:
        idf[word] = math.log(total_documents / (idf[word] + 1))
    return idf

# Calculate TF-IDF scores for each review (whole sentence)
def calculate_tf_idf(data):
    tf_idf_scores = {}
    idf = calculate_idf(data)
    for index, row in data.iterrows():
        review = row['Review Text']
        print(review)
        words = preprocess_text(review)
        tf = calculate_tf(words)
        tf_idf = {}
        for word in words:
            tf_idf[word] = tf[word] * idf.get(word, 0)
        # Concatenate all TF-IDF scores into a single vector
        tf_idf_vector = np.array(list(tf_idf.values()))
        tf_idf_scores[review] = tf_idf_vector
    return tf_idf_scores

csv_file = "/content/drive/MyDrive/A2_Data.csv"
# Read CSV file
df = pd.read_csv(csv_file)
tf_idf_dict = calculate_tf_idf(df)

<ipython-input-13-f00c96aa4ef3>:6: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  clean_text = BeautifulSoup(text, 'html.parser').get_text()


Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.
Works great as a guitar bench mat. Not rugged enough for abuse but if you take care of it, it will take care of you. Makes organization of workspace much easier because screws won't roll around. Color is good too.
We use these for everything from our acoustic bass down to our ukuleles. I know there is a smaller model available for ukes, violins, etc.; we haven't yet ordered those, but these will work on smaller instruments if one doesn't extend the feet to their maximum width. They're gentle on the instruments, and the grippy material keeps them secure.

The greatest benefit has been when writing music at the computer and needing to set a guitar down to use the keyboard/mouse - just easier for me than a hanging stand.

We have several and gave one to a friend for Christmas as well. I've used m

In [14]:
print(tf_idf_dict)

{'Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.': array([0.35322116, 0.52844217, 0.64377516, 0.21978916, 0.10532527,
       0.31403538, 0.07575428, 0.34106639, 0.36809739, 0.22349381,
       0.17180146, 0.17357935, 0.15622714]), "Works great as a guitar bench mat. Not rugged enough for abuse but if you take care of it, it will take care of you. Makes organization of workspace much easier because screws won't roll around. Color is good too.": array([0.07383779, 0.04940496, 0.05472961, 0.25257143, 0.25257143,
       0.2157324 , 0.10981429, 0.24006352, 0.25877649, 0.36519175,
       0.09328615, 0.27020035, 0.27020035, 0.09403579, 0.16796665,
       0.11817828, 0.14701716, 0.20992668, 0.12020089, 0.13024923,
       0.0686904 ]), "We use these for everything from our acoustic bass down to our ukuleles. I know there is a smaller model available

In [16]:
print(tf_idf_dict["Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go."])

[0.35322116 0.52844217 0.64377516 0.21978916 0.10532527 0.31403538
 0.07575428 0.34106639 0.36809739 0.22349381 0.17180146 0.17357935
 0.15622714]


**save in pickal file**

In [17]:
# File path where you want to save the pickle file
pickle_file_path = "/content/text_feature.pickle"

# Open the file in binary write mode
with open(pickle_file_path, "wb") as pickle_file:
    # Dump the dictionary into the pickle file
    pickle.dump(tf_idf_dict, pickle_file)
print("Data has been saved to", pickle_file_path)

Data has been saved to /content/text_feature.pickle


open the pickle file

In [18]:
# File path where the pickle file is stored
pickle_file_path = "/content/text_feature.pickle"

# Open the pickle file in binary read mode
with open(pickle_file_path, "rb") as pickle_file:
    # Load the dictionary from the pickle file
    loaded_dict_text = pickle.load(pickle_file)

# Now you can use the loaded dictionary
print("Data loaded from pickle file:", loaded_dict_text)

Streaming output truncated to the last 5000 lines.
       0.09227784, 0.11639075, 0.13463147, 0.07317381, 0.07035918,
       0.04498048, 0.07317423, 0.08280408, 0.08280408, 0.0671328 ,
       0.07492927, 0.08605708, 0.05881385, 0.12118869, 0.1394294 ,
       0.16354232]), 'This is a fantastic rack and makes my home studio look really professional.': array([0.46110993, 0.51689582, 0.26819767, 0.47153263, 0.39044571,
       0.22675063, 0.24938755, 0.51689582]), "If you're looking for an inexpensive party light, this is a great option.  The beams are pretty tight and is really set off with a fog machine.  The speaker inside was shocking at first (when you plug it in there is a commanding voice talking about bluetooth connectivity.)  There is a little wireless remote that is useful within 10 feet or so.  The motor is a bit loud but with music playing you won't notice.\n\nThere is one piece of functionality that I'm not sure about, and that's music sync.  I don't intend to serve music from 

In [19]:
print(loaded_dict_text["Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go."])

[0.35322116 0.52844217 0.64377516 0.21978916 0.10532527 0.31403538
 0.07575428 0.34106639 0.36809739 0.22349381 0.17180146 0.17357935
 0.15622714]


In [21]:
# Define the two vectors
vector1 = np.array([0.35322116, 0.52844217, 0.64377516, 0.21978916, 0.10532527, 0.34106639, 0.36809739, 0.22349381, 0.17180146, 0.17357935, 0.15622714])
vector2 = np.array([0.07383779, 0.04940496, 0.05472961, 0.25257143, 0.25257143, 0.2157324,
  0.10981429, 0.24006352, 0.25877649, 0.36519175, 0.09328615, 0.27020035,
  0.27020035, 0.09403579, 0.16796665, 0.11817828, 0.14701716, 0.20992668,
  0.12020089, 0.13024923, 0.0686904 ])


# Find the dimension of the longer vector
max_dim = max(len(vector1), len(vector2))

# Pad the shorter vector with zeros to make it the same dimension as the longer vector
if len(vector1) < max_dim:
    vector1 = np.pad(vector1, (0, max_dim - len(vector1)), mode='constant')
elif len(vector2) < max_dim:
    vector2 = np.pad(vector2, (0, max_dim - len(vector2)), mode='constant')

# Reshape the vectors to make them compatible for cosine similarity calculation


# Calculate the cosine similarity between the two vectors
cos_sim = cosine_similarity(vector1, vector2)
print("Cosine Similarity:", cos_sim)

Cosine Similarity: 0.46819545512943717


**mapping the url and its crossponding text**

In [22]:
csv_file = "/content/drive/MyDrive/A2_Data.csv"
# Read CSV file
df = pd.read_csv(csv_file)

# Initialize an empty dictionary to store URL-review text pairs
url_review_dict = {}

# Iterate through each row of the dataset
for index, row in df.iterrows():
    # Extract the URLs from the "Image" column
    urls = row['Image'].strip("[]").replace("'", "").split(", ")
    review_text = row['Review Text']
    # Create a key-value pair for each URL and its corresponding review text
    for url in urls:
        url_review_dict[url.strip()] = review_text

# Display the dictionary
for url, review_text in url_review_dict.items():
    print("URL:", url)
    print("Review Text:", review_text)
    print()

Streaming output truncated to the last 5000 lines.
URL: https://images-na.ssl-images-amazon.com/images/I/712ADmGWGVL._SY88.jpg
Review Text: Awesome bass. I love it. As some other reviewers have commented this bass is not balanced as a standard solid body bass. the neck is definitely heavier due to the hollow body, but you know, that's the way it goes. I love the sound the hollow body gives you sounds a bit like my acoustic bass. The controls give a nice variety of sounds. I am something of a novice player but wanted to add a hollow body bass to my small collection and this Hofner replica is just the ticket. I think I might replace the strings that it came with as they sound a too metallic for my taste, but they are playable and hold tune well. I was able to play this bass right out of the box once I tuned it. No need for adjusting and didn't have that fret buss some reviewers have commented on. I did notice the neck is slimmer and the strings are closer together than any of my other ba

In [41]:
print(url_review_dict)

{'https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg': 'Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.', 'https://images-na.ssl-images-amazon.com/images/I/71HSx4Y-5dL._SY88.jpg': "Works great as a guitar bench mat. Not rugged enough for abuse but if you take care of it, it will take care of you. Makes organization of workspace much easier because screws won't roll around. Color is good too.", 'https://images-na.ssl-images-amazon.com/images/I/71dVsYejzTL._SY88.jpg': "Works great as a guitar bench mat. Not rugged enough for abuse but if you take care of it, it will take care of you. Makes organization of workspace much easier because screws won't roll around. Color is good too.", 'https://images-na.ssl-images-amazon.com/images/I/71domStNfIL._SY88.jpg': "Works great as a guitar bench mat. Not rugged enough for abuse but if

In [24]:
pickle_file_path = "/content/url_review_dict.pickle"

# Open the file in binary write mode
with open(pickle_file_path, "wb") as pickle_file:
    # Dump the dictionary into the pickle file
    pickle.dump(url_review_dict, pickle_file)
print("Data has been saved to", pickle_file_path)

Data has been saved to /content/url_review_dict.pickle


In [42]:
# File path where the pickle file is stored
pickle_file_path = "/content/url_review_dict.pickle"

# Open the pickle file in binary read mode
with open(pickle_file_path, "rb") as pickle_file:
    # Load the dictionary from the pickle file
    url_review_dict_lodaded = pickle.load(pickle_file)
# Now you can use the loaded dictionary
print("Data loaded from pickle file:", url_review_dict_lodaded)

Data loaded from pickle file: {'https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg': 'Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.', 'https://images-na.ssl-images-amazon.com/images/I/71HSx4Y-5dL._SY88.jpg': "Works great as a guitar bench mat. Not rugged enough for abuse but if you take care of it, it will take care of you. Makes organization of workspace much easier because screws won't roll around. Color is good too.", 'https://images-na.ssl-images-amazon.com/images/I/71dVsYejzTL._SY88.jpg': "Works great as a guitar bench mat. Not rugged enough for abuse but if you take care of it, it will take care of you. Makes organization of workspace much easier because screws won't roll around. Color is good too.", 'https://images-na.ssl-images-amazon.com/images/I/71domStNfIL._SY88.jpg': "Works great as a guitar bench mat. Not 

In [43]:
print(url_review_dict_lodaded["https://images-na.ssl-images-amazon.com/images/I/61cej6M43zL._SY88.jpg"])

I bought It to storage my Epiphone Les Paul Standard, It fits perfect, the inside is soft, this case provides a great protection, It's a little heavy, but I think this is the best choice for a epi LP.


**feature extraction of url**

In [44]:
def get_vgg16_feature_vector(image_url):
    try:
        # Remove any extra characters like single quotes, double quotes, and spaces
        image_url = image_url.strip("[]\"' ")

        # Check if the URL starts with 'http://' or 'https://'
        if not image_url.startswith("http://") and not image_url.startswith("https://"):
            image_url = "http://" + image_url  # Add 'http://' if missing

        #print("Downloading image from:", image_url)  # Print the URL for debugging

        # Send a GET request to download the image
        response = requests.get(image_url)
        if response.status_code == 200:
            # Decode the content of the image
            image_data = response.content
            # Convert image data to numpy array
            nparr = np.frombuffer(image_data, np.uint8)
            # Read image from numpy array
            image = cv2.imdecode(nparr, cv2.IMREAD_COLOR)
            # Resize image to the input size of VGG16 (224x224)
            resized_image = cv2.resize(image, (224, 224))

            # Convert BGR to RGB (VGG16 expects RGB images)
            resized_image = cv2.cvtColor(resized_image, cv2.COLOR_BGR2RGB)

            # Normalize pixel values to range [0, 1]
            resized_image = resized_image.astype("float32") / 255.0

            # Load pre-trained VGG16 model without the top classification layer
            vgg16 = VGG16(weights='imagenet', include_top=False, input_shape=(224, 224, 3))

            # Create a model with VGG16 up to a certain layer
            feature_extractor = Model(inputs=vgg16.input, outputs=vgg16.get_layer('block5_conv2').output)

            # Preprocess the image
            image = preprocess_input(np.expand_dims(resized_image, axis=0))

            # Extract features using VGG16 model
            features = feature_extractor.predict(image)
            # Flatten the features
            features = features.flatten()

            return features
        else:
            print("Failed to download image from:", image_url)
            return None
    except Exception as e:
        print("Error:", e)
        return None

In [45]:
# Function to preprocess text
def preprocess_text(text):
    try:
        # Ensure text is a string
        text = str(text)
        # Remove HTML tags using BeautifulSoup
        clean_text = BeautifulSoup(text, 'html.parser', features="html.parser").get_text()
    except:
        # If BeautifulSoup raises an exception, assume the input is already clean text
        clean_text = text
    # Convert to lowercase
    clean_text = clean_text.lower()
    # Tokenize
    tokens = word_tokenize(clean_text)
    # Remove stopwords and non-alphabetic tokens
    stop_words = set(stopwords.words('english'))
    words = [word for word in tokens if word.isalpha() and word not in stop_words]
    # Lemmatization
    lemmatizer = WordNetLemmatizer()
    words = [lemmatizer.lemmatize(word) for word in words]
    return words

# Function to calculate term frequency (TF)
def calculate_tf(words):
    word_count = len(words)
    term_frequency = {}
    word_freq = Counter(words)
    for word in word_freq:
        term_frequency[word] = word_freq[word] / word_count
    return term_frequency

# Function to calculate inverse document frequency (IDF)
def calculate_idf(data):
    total_documents = len(data)
    idf = {}
    for index, row in data.iterrows():
        review = row['Review Text']
        words = set(preprocess_text(review))
        for word in words:
            idf[word] = idf.get(word, 0) + 1
    for word in idf:
        idf[word] = math.log(total_documents / (idf[word] + 1))
    return idf

# Calculate TF-IDF scores for each review (whole sentence)
def calculate_tf_idf(data , review_text):
    tf_idf_scores = {}
    idf = calculate_idf(data)
    words = preprocess_text(review_text)
    tf = calculate_tf(words)
    tf_idf = {}
    for word in words:
        tf_idf[word] = tf[word] * idf.get(word, 0)
        # Concatenate all TF-IDF scores into a single vector
        tf_idf_vector = np.array(list(tf_idf.values()))
        tf_idf_scores[review_text] = tf_idf_vector
    return tf_idf_scores

In [46]:
csv_file = "/content/drive/MyDrive/A2_Data.csv"
df = pd.read_csv(csv_file)
review_text = "Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go."
tf_idf_dict = calculate_tf_idf(df , review_text)

In [47]:
print(tf_idf_dict)

{'Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.': array([0.35322116, 0.52844217, 0.64377516, 0.21978916, 0.10532527,
       0.31403538, 0.07575428, 0.34106639, 0.36809739, 0.22349381,
       0.17180146, 0.17357935, 0.15622714])}


In [50]:
# Example vectors
def image_preprocessing(feature):
    vector2 = np.array(feature)
    result ={}
    for url in data_dict.keys():
       vector1 = np.array(data_dict[url])
       similarity = cosine_similarity(vector1, vector2)
       result[url] = similarity
    sorted_dict = dict(sorted(result.items(), key=lambda x: x[1],reverse=True))
    return sorted_dict

In [53]:
def cosinemacting(ress1 , ress2):
   vector1 = np.array(ress1)
   vector2 = np.array(ress2)
   result ={}
   max_dim = max(len(vector1), len(vector2))
   if len(vector1) < max_dim:
      vector1 = np.pad(vector1, (0, max_dim - len(vector1)), mode='constant')
   elif len(vector2) < max_dim:
      vector2 = np.pad(vector2, (0, max_dim - len(vector2)), mode='constant')

   # Calculate the cosine similarity between the two vectors
   cos_sim = cosine_similarity(vector1, vector2)
   return cos_sim

In [33]:
print(np.array(loaded_dict_text["Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go."]))

[0.35322116 0.52844217 0.64377516 0.21978916 0.10532527 0.31403538
 0.07575428 0.34106639 0.36809739 0.22349381 0.17180146 0.17357935
 0.15622714]


In [34]:
loaded_dict_text

{'Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.': array([0.35322116, 0.52844217, 0.64377516, 0.21978916, 0.10532527,
        0.31403538, 0.07575428, 0.34106639, 0.36809739, 0.22349381,
        0.17180146, 0.17357935, 0.15622714]),
 "Works great as a guitar bench mat. Not rugged enough for abuse but if you take care of it, it will take care of you. Makes organization of workspace much easier because screws won't roll around. Color is good too.": array([0.07383779, 0.04940496, 0.05472961, 0.25257143, 0.25257143,
        0.2157324 , 0.10981429, 0.24006352, 0.25877649, 0.36519175,
        0.09328615, 0.27020035, 0.27020035, 0.09403579, 0.16796665,
        0.11817828, 0.14701716, 0.20992668, 0.12020089, 0.13024923,
        0.0686904 ]),
 "We use these for everything from our acoustic bass down to our ukuleles. I know there is a smaller model a

In [ ]:
for key, value in loaded_dict_text.items():
  print(value)

**finding cosine similarity**

In [52]:
def cosine_similarity_different_sizes(v1, v2):
    # Convert vectors to numpy arrays
    v1 = np.array(v1)
    v2 = np.array(v2)

    # Pad the shorter vector with zeros to match the length of the longer vector
    max_dim = max(len(v1), len(v2))
    if len(v1) < max_dim:
        v1 = np.pad(v1, (0, max_dim - len(v1)), mode='constant')
    elif len(v2) < max_dim:
        v2 = np.pad(v2, (0, max_dim - len(v2)), mode='constant')

    # Calculate cosine similarity
    similarity = cosine_similarity(v1, v2)

    return similarity

In [37]:
def textpreprocessing(v1):
  ress = {}
  for key, value in loaded_dict_text.items():
      similarity_score = cosine_similarity_different_sizes(v1, value)
      ress[key] = similarity_score
  ress_sorted = dict(sorted(ress.items(), key=lambda item: item[1], reverse=True))
  return ress_sorted

In [ ]:
url_review_dict_lodaded

search url crossponding to its value

In [39]:
def searchurl(text):
  for key, value in url_review_dict_lodaded.items():
    if(value == text):
       return key

**search engine that take input or output**

In [54]:
print("Input")
combined ={}
print("Image and Text Query Input :")
image_url = input("Image: ")
review_text = input("Review: ")
feature_vector = get_vgg16_feature_vector(image_url)
res ={}
res = image_preprocessing(feature_vector)
csv_file = "/content/drive/MyDrive/A2_Data.csv"
df = pd.read_csv(csv_file)
tf_idf_dict = calculate_tf_idf(df , review_text)

print("USING IMAGE RETRIEVAL")
for i, (url, value) in enumerate(res.items()):
    if i == 3:
        break
    print(f"Image URL: {url}")
    print("")
    print(f"Review: {url_review_dict_lodaded[url]}")
    print("")
    print(f"Cosine similarity of images: {value}")
    print("")
    textcosine = cosinemacting(tf_idf_dict[review_text] ,loaded_dict_text[url_review_dict_lodaded[url]])
    print(f"Cosine similarity of text: {textcosine}")
    print("")
    print(f"Combined Cosine similarity of text: {(value + textcosine) /2}")
    combined[url] = (value + textcosine) /2
    print("")

print("---------------------------------------------------------------------")
print("---------------------------------------------------------------------")
resss={}
tf_idf_dict = calculate_tf_idf(df , review_text)
tf_idf_score = tf_idf_dict.get(review_text)
resss =textpreprocessing(tf_idf_score)
print("USING TEXT RETRIEVAL")
for j, (text, value) in enumerate(resss.items()):
    if j == 3:
        break
    uurl = searchurl(text)
    print(f"Image URL: {searchurl(text)}")
    feature_vector = get_vgg16_feature_vector(uurl)
    res ={}
    res = image_preprocessing(feature_vector)
    first_key = next(iter(res))
    print("")
    print(f"Review: {text}")
    print("")
    print(f"Cosine similarity of images: {res[first_key]}")
    print("")
    print(f"Cosine similarity of text: {value}")
    print("")
    print(f"Combined Cosine similarity of text: {(res[first_key] + value) /2}")
    print("")

    compositesimilarityscore = (res[first_key] + value) /2
    for key, v in combined.items():
       if(key == uurl):
          compositesimilarityscore = max(compositesimilarityscore , combined[key])
    combined[searchurl(text)] = compositesimilarityscore

print("------------------------------------------------------------------------------")
print("------------------------------------------------------------------------------")

print("USING COBINED RETRIEVAL")
#combined retrival
ress_combined = dict(sorted(combined.items(), key=lambda item: item[1], reverse=True))
for top, (url, value) in enumerate(ress_combined.items()):
    if top == 3:
        break
    print(f"Image URL: {url}")
    print("")
    print(f"Review: {url_review_dict_lodaded[url]}")
    print("")
    print(f"Combined similarity : {value}")
    print("")

Input
Image and Text Query Input :
Image: https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg
Review: Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.
1/1 [==============================] - 1s 618ms/step
USING IMAGE RETRIEVAL
Image URL: https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg

Review: Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.

Cosine similarity of images: 1.0

Cosine similarity of text: 0.9999999999999999

Combined Cosine similarity of text: 1.0

Image URL: https://images-na.ssl-images-amazon.com/images/I/5145Rvuj71L._SY88.jpg

Review: My oldest son plays and owns many guitars. He asked for a new guitar strap for Christmas. I ordered this on

1/1 [==============================] - 1s 1s/step

Review: Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.

Cosine similarity of images: 1.0

Cosine similarity of text: 0.9999999999999999

Combined Cosine similarity of text: 1.0

Image URL: https://images-na.ssl-images-amazon.com/images/I/71nJnXwE9XL._SY88.jpg


1/1 [==============================] - 1s 1s/step

Review: This bridge is beyond iconic and needed for any Telecaster build. Looks beautiful on any body that you put it on!

Cosine similarity of images: 1.0000001192092896

Cosine similarity of text: 0.9300903833529373

Combined Cosine similarity of text: 0.9650452512811134

Image URL: https://images-na.ssl-images-amazon.com/images/I/71JH6s-YDeL._SY88.jpg
1/1 [==============================] - 1s 594ms/step

Review: I have tried several violin strings and these are the ones I will buy again and again. Over all great even tone. Not to bright but clear.

Cosine similarity of images: 1.0

Cosine similarity of text: 0.9249676054187196

Combined Cosine similarity of text: 0.9624838027093598

------------------------------------------------------------------------------
------------------------------------------------------------------------------
USING COBINED RETRIEVAL
Image URL: https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL.